In [59]:
import numpy as np
import pandas as pd
import datetime

from Project.Database import Db
from Project._05InferKnowledgeOfRules.infer_rules_functions import json_to_dataframe

# Phase 1
Define available appliances

In [60]:
meta = Db.load_data(meta=True, hourly=False, consumption=False)
appliance_list = meta.loc[(lambda self:
                           (self["Parameter"] == "Status_OnOff") &
                           (~ self.index.str.contains("SensHeat")) &
                           (~ self.index.str.contains("Cold")))].index.to_list()
appliance_list

['DHW_StatusSolenoidHotKitchenSink',
 'DHW_StatusSolenoidHotMBAShower',
 'DHW_StatusSolenoidHotMBATub',
 'Load_StatusApplianceCooktop',
 'Load_StatusApplianceDishwasher',
 'Load_StatusApplianceOven',
 'Load_StatusApplianceRangeHood',
 'Load_StatusBA1Lights',
 'Load_StatusBA2Lights',
 'Load_StatusBR2Lights',
 'Load_StatusBR3Lights',
 'Load_StatusBR4Lights',
 'Load_StatusDRLights',
 'Load_StatusEntryHallLights',
 'Load_StatusKitchenLightsA',
 'Load_StatusKitchenLightsB',
 'Load_StatusKitchenLightsC',
 'Load_StatusLRLights1',
 'Load_StatusLRLights2',
 'Load_StatusLRLights3',
 'Load_StatusLatentload',
 'Load_StatusMBALights',
 'Load_StatusMBRLights1',
 'Load_StatusMBRLights2',
 'Load_StatusPlugLoadBR2Laptop',
 'Load_StatusPlugLoadBR3Laptop',
 'Load_StatusPlugLoadBlender',
 'Load_StatusPlugLoadCanOpener',
 'Load_StatusPlugLoadCoffeeMaker',
 'Load_StatusPlugLoadDesktopPCMonitor',
 'Load_StatusPlugLoadFan',
 'Load_StatusPlugLoadHairDryerCurlIron',
 'Load_StatusPlugLoadHandMixer',
 'Load_Statu

In [68]:
meta[['Load_Match', 'Elec_Match', 'DHW_Match']]

Load_Match  \
Unnamed: 0                                                                    
DHW_ClothesWasherColdFlow                                               NaN   
DHW_ClothesWasherHotFlow                                                NaN   
DHW_DishwasherHotFlow                                                   NaN   
DHW_HeatPumpWaterHeaterEnergyTotal                                      NaN   
DHW_HeatPumpWaterHeaterPowerTotal                                       NaN   
...                                                                     ...   
HVAC_HeatPumpIndoorUnitPower                                            NaN   
HVAC_HeatPumpOutdoorUnitPower                                           NaN   
Load_StatusClothesWasher                 Load_ClothesWasherPowerWithStandby   
Load_StatusDryerPowerTotal                             Load_DryerPowerTotal   
DHW_StatusHeatPumpWaterHeaterPowerTotal                                 NaN   

                                                       Elec_Match  \
Unnamed: 0                                                          
DHW_ClothesWasherColdFlow                                     NaN   
DHW_ClothesWasherHotFlow                                      NaN   
DHW_DishwasherHotFlow                                         NaN   
DHW_HeatPumpWaterHeaterEnergyTotal                            NaN   
DHW_HeatPumpWaterHeaterPowerTotal                             NaN   
...                                                           ...   
HVAC_HeatPumpIndoorUnitPower                                  NaN   
HVAC_HeatPumpOutdoorUnitPower                                 NaN   
Load_StatusClothesWasher                  Elec_PowerClothesWasher   
Load_StatusDryerPowerTotal                    Elec_PowerDryer1of2   
DHW_StatusHeatPumpWaterHeaterPowerTotal  Elec_PowerHeatPumpWH2of2   

                                                                 DHW_Match  
Unnamed: 0                                                                  
DHW_ClothesWasherColdFlow                                              NaN  
DHW_ClothesWasherHotFlow                                               NaN  
DHW_DishwasherHotFlow                                                  NaN  
DHW_HeatPumpWaterHeaterEnergyTotal                                     NaN  
DHW_HeatPumpWaterHeaterPowerTotal                                      NaN  
...                                                                    ...  
HVAC_HeatPumpIndoorUnitPower                                           NaN  
HVAC_HeatPumpOutdoorUnitPower                                          NaN  
Load_StatusClothesWasher                                               NaN  
Load_StatusDryerPowerTotal                                             NaN  
DHW_StatusHeatPumpWaterHeaterPowerTotal  DHW_HeatPumpWaterHeaterPowerTotal  

[335 rows x 3 columns]

# Phase 2
Find constraints of devices:
o	If there are hard constraints for this appliance only
o	Does it have to be on in a continous period of time? How long does it last?
o	How many watts pr second does it use?
o	How much energy does it need from start to finish?


In [74]:
level1_rules = json_to_dataframe(year=2, level=1)
level1_rules

pattern      supp  conf  \
0            Load_StatusSensHeatPrntAUP  0.991781   1.0   
1            Load_StatusSensHeatPrntBUP  0.991781   1.0   
2           Load_StatusSensHeatChildAUP  0.991781   1.0   
3           Load_StatusSensHeatChildBUP  0.991781   1.0   
4                  Load_StatusMBALights  0.991781   1.0   
5          Load_StatusSensHeatPrntBDOWN  0.991781   1.0   
6          Load_StatusSensHeatPrntADOWN  0.991781   1.0   
7         Load_StatusApplianceRangeHood  0.991781   1.0   
8           Load_StatusApplianceCooktop  0.991781   1.0   
9              Load_StatusApplianceOven  0.287671   1.0   
10             Load_StatusKitchenLights  0.991781   1.0   
11              Load_StatusPlugLoadLRTV  0.991781   1.0   
12  Load_StatusPlugLoadDesktopPCMonitor  0.991781   1.0   
13                 Load_StatusBA2Lights  0.991781   1.0   
14        Load_StatusSensHeatChildADOWN  0.991781   1.0   
15       Load_StatusPlugLoadCoffeeMaker  0.989041   1.0   
16           Load_StatusPlugLoadBlender  0.989041   1.0   
17       Load_StatusPlugLoadToasterOven  0.989041   1.0   
18           Load_StatusPlugLoadToaster  0.989041   1.0   
19                  Load_StatusDRLights  0.991781   1.0   
20        Load_StatusSensHeatChildBDOWN  0.991781   1.0   
21         Load_StatusPlugLoadVideoGame  0.430137   1.0   
22       Load_StatusMasterBedroomLights  0.991781   1.0   
23         Load_StatusPlugLoadBR2Laptop  0.991781   1.0   
24             Load_StatusClothesWasher  0.427397   1.0   
25           Load_StatusDryerPowerTotal  0.432877   1.0   
26              Load_StatusPlugLoadIron  0.287671   1.0   
27         Load_StatusPlugLoadLRBlueRay  0.287671   1.0   
28          Load_StatusLivingRoomLights  0.991781   1.0   
29                 Load_StatusBA1Lights  0.991781   1.0   
30                 Load_StatusBR2Lights  0.989041   1.0   
31                 Load_StatusBR3Lights  0.991781   1.0   
32         Load_StatusPlugLoadBR3Laptop  0.991781   1.0   
33         Load_StatusPlugLoadHandMixer  0.991781   1.0   
34         Load_StatusPlugLoadCanOpener  0.991781   1.0   
35       Load_StatusApplianceDishwasher  0.712329   1.0   
36             Load_StatusPlugLoadMBRTV  0.846575   1.0   
37        Load_StatusPlugLoadMBRBlueRay  0.284932   1.0   
38               Load_StatusPlugLoadFan  0.989041   1.0   
39        Load_StatusPlugLoadHeatingPad  0.989041   1.0   
40        Load_StatusPlugLoadSlowCooker  0.279452   1.0   
41            Load_StatusPlugLoadVacuum  0.142466   1.0   

                                                 time  
0   {'0': [['2015-02-01 00:04:50', '2015-02-01 08:...  
1   {'0': [['2015-02-01 00:04:50', '2015-02-01 08:...  
2   {'0': [['2015-02-01 00:04:50', '2015-02-01 08:...  
3   {'0': [['2015-02-01 00:04:50', '2015-02-01 08:...  
4   {'0': [['2015-02-01 07:59:49', '2015-02-01 08:...  
5   {'0': [['2015-02-01 08:14:49', '2015-02-01 09:...  
6   {'0': [['2015-02-01 08:14:49', '2015-02-01 09:...  
7   {'0': [['2015-02-01 08:14:49', '2015-02-01 08:...  
8   {'0': [['2015-02-01 08:14:49', '2015-02-01 08:...  
9   {'0': [['2015-02-01 08:14:49', '2015-02-01 10:...  
10  {'0': [['2015-02-01 08:14:49', '2015-02-01 09:...  
11  {'0': [['2015-02-01 08:29:49', '2015-02-01 10:...  
12  {'0': [['2015-02-01 08:29:49', '2015-02-01 18:...  
13  {'0': [['2015-02-01 08:44:49', '2015-02-01 09:...  
14  {'0': [['2015-02-01 08:59:49', '2015-02-01 10:...  
15  {'0': [['2015-02-01 09:09:49', '2015-02-01 09:...  
16  {'0': [['2015-02-01 09:14:49', '2015-02-01 09:...  
17  {'0': [['2015-02-01 09:19:49', '2015-02-01 09:...  
18  {'0': [['2015-02-01 09:19:49', '2015-02-01 09:...  
19  {'0': [['2015-02-01 09:29:49', '2015-02-01 09:...  
20  {'0': [['2015-02-01 09:29:49', '2015-02-01 09:...  
21  {'0': [['2015-02-01 09:59:49', '2015-02-01 10:...  
22  {'0': [['2015-02-01 10:14:49', '2015-02-01 10:...  
23  {'0': [['2015-02-01 10:59:49', '2015-02-01 12:...  
24  {'0': [['2015-02-01 11:00:49', '2015-02-01 11:...  
25  {'0': [['2015-02-01 12:30:49', '20

In [75]:
time_delta_dict = {}
for index, row in level1_rules.iterrows():
    if 'SensHeat' not in row['pattern']:
        time_delta_dict[row["pattern"]] = pd.Series(dtype='float64')
        for intervals in row["time"].values():
           for interval in intervals:
               time_delta_dict[row["pattern"]] = pd.concat((time_delta_dict[row["pattern"]], pd.Series((pd.to_datetime(interval[1], format="%Y-%m-%d %H:%M:%S") - pd.to_datetime(interval[0], format="%Y-%m-%d %H:%M:%S")).total_seconds()/60)), ignore_index=True)


In [76]:
time_delta_dict['Load_StatusApplianceDishwasher'].describe()

count    260.000000
mean     135.282115
std       51.621602
min       28.000000
25%      131.000000
50%      132.000000
75%      132.000000
max      937.433333
dtype: float64

In [77]:
time_delta_dict['Load_StatusClothesWasher'][lambda self: self <130]

0      57.000000
1      57.983333
2      57.000000
3      57.000000
4      56.983333
         ...    
307    55.983333
308    58.000000
309    56.983333
310    56.000000
311    62.000000
Length: 312, dtype: float64

In [80]:
import plotly.express as px
hist = pd.Series(time_delta_dict["Load_StatusApplianceDishwasher"])
fig = px.histogram(hist)
fig.show()

In [79]:
fig = px.box(time_delta_dict, log_y=True)
fig.show()

# Phase 3
Maybe the patterns can help some of the constraints
    o	Washing machine can be used at every hour, but maybe the constraints of the user can be found in the patterns
        	E.g. General constraint that the appliances cant be started when the users are not home
        	Dryer have to be started after the clotheswasher, so the clotheswasher cannot be started right before they go out of the house.